# setup

In [ ]:
!pip install jsonschema==3.2  #using until altair addresses schema issue
!pip install geopandas
!pip install sodapy
!pip install cenpy
!pip install jenkspy
import numpy as np
import pandas as pd
import geopandas as gpd
import altair as alt
import cenpy as cen
import cenpy.tiger as tiger
import jenkspy
from getpass import getpass
import numpy as np
from shapely.geometry import Polygon

     |████████████████████████████████| 56 kB 2.1 MB/s 
  Attempting uninstall: jsonschema
    Found existing installation: jsonschema 4.3.3
    Uninstalling jsonschema-4.3.3:
      Successfully uninstalled jsonschema-4.3.3
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
nbclient 0.6.2 requires jupyter-client>=6.1.5, but you have jupyter-client 5.3.5 which is incompatible.
     |████████████████████████████████| 1.0 MB 12.5 MB/s 
     |████████████████████████████████| 6.3 MB 65.9 MB/s 
     |████████████████████████████████| 16.7 MB 335 kB/s 
     |████████████████████████████████| 1.0 MB 17.8 MB/s 
     |████████████████████████████████| 2.4 MB 75.7 MB/s 
  Created wheel for cenpy: filename=cenpy-1.0.0.post4-py3-none-any.whl size=29924 sha256=ab7fc5c260ff69fdfe80b6160ca839e5ffa362569bfcb7a5df30d9a9bcf3f47f
  Stored in directory: /root/.cache/pip/wheels/3c/6a/

/usr/local/lib/python3.7/dist-packages/fuzzywuzzy/fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [ ]:
from google.colab import files

BWCmeta = files.upload()

for fn in BWCmeta.keys():
  print('User uploaded file "{name}" with length {length} bytes'.format(
      name=fn, length=len(BWCmeta[fn])))

Saving NOPD_Body_Worn_Camera_Metadata (1).csv to NOPD_Body_Worn_Camera_Metadata (1).csv
User uploaded file "NOPD_Body_Worn_Camera_Metadata (1).csv" with length 26831695 bytes


In [ ]:
BWCmeta = pd.read_csv('/content/NOPD_Body_Worn_Camera_Metadata (1).csv')

# ACTIVATION POINTS

In [ ]:
BWCmeta = BWCmeta.drop(BWCmeta[BWCmeta['location'].isna()].index)

In [ ]:
BWCmetaGEO = gpd.GeoDataFrame(BWCmeta, geometry=gpd.points_from_xy(BWCmeta.longitude, BWCmeta.latitude))

In [ ]:
BWCmetaGEO.to_file("BWC.geojson", na='drop', driver="GeoJSON")

KeyboardInterrupt: ignored

In [ ]:
BWCmetaGEO = BWCmetaGEO.set_crs('epsg:4326')

# SHAPE FILE SET UP

In [ ]:
louisianaSHP = gpd.read_file ('https://www2.census.gov/geo/tiger/GENZ2020/shp/cb_2020_22_tract_500k.zip')

In [ ]:
louisianaSHP = louisianaSHP.to_crs('EPSG:4326')

In [ ]:
louisianaSHP.head(1)

STATEFP COUNTYFP TRACTCE              AFFGEOID        GEOID NAME  \
0      22      033  003400  1400000US22033003400  22033003400   34   

          NAMELSAD STUSPS               NAMELSADCO STATE_NAME LSAD    ALAND  \
0  Census Tract 34     LA  East Baton Rouge Parish  Louisiana   CT  4491465   

   AWATER                                           geometry  
0       0  POLYGON ((-91.14850 30.51291, -91.14755 30.515...

In [ ]:
neworleansSHP = louisianaSHP[louisianaSHP['COUNTYFP'] == '071'] 

In [ ]:
neworleansSHP.head()

STATEFP COUNTYFP TRACTCE              AFFGEOID        GEOID   NAME  \
16      22      071  004600  1400000US22071004600  22071004600     46   
17      22      071  003302  1400000US22071003302  22071003302  33.02   
18      22      071  003400  1400000US22071003400  22071003400     34   
19      22      071  011600  1400000US22071011600  22071011600    116   
20      22      071  009400  1400000US22071009400  22071009400     94   

              NAMELSAD STUSPS      NAMELSADCO STATE_NAME LSAD    ALAND  \
16     Census Tract 46     LA  Orleans Parish  Louisiana   CT   702695   
17  Census Tract 33.02     LA  Orleans Parish  Louisiana   CT  1682319   
18     Census Tract 34     LA  Orleans Parish  Louisiana   CT   373145   
19    Census Tract 116     LA  Orleans Parish  Louisiana   CT   362832   
20     Census Tract 94     LA  Orleans Parish  Louisiana   CT   528802   

    AWATER                                           geometry  
16   27900  POLYGON ((-90.10509 29.98379, -90.10273 29.984...  
17   80725  POLYGON ((-90.08530 30.00665, -90.08499 30.008...  
18       0  POLYGON ((-90.07124 29.97127, -90.06838 29.974...  
19       0  POLYGON ((-90.12152 29.92214, -90.12086 29.923...  
20       0  POLYGON ((-90.10220 29.95396, -90.09828 29.951...

In [ ]:
BWCmetaGEO.head()

evidence_id  status  \
0  92F109F4-DC36-42C3-9FFE-2EB223A5F67F  Active   
1  FAC99FF5-6388-4CF6-9FCD-51914BEDA938  Active   
3  A751D1B2-CF80-4B22-A11A-F08DE7340219  Active   
4  0EA9EFD1-31E2-42A1-8D78-AE3459CDC44A  Active   
5  2BA89B28-6E32-4156-BBBC-40922D1FA271  Active   

                               title id_external  \
0                    1421 GEN TAYLOR  L-37827-20   
1                   929 S TELEMACHUS  L-37936-20   
3  Axon Body 3 Video 2020-12-31 1817         NaN   
4                     SIXTH DISTRICT  L-00000-20   
5                         Accidental   L-0000-20   

                   date_uploaded      created_date_record_start  \
0  2021-01-01T00:00:38.795-06:00  2020-12-31T18:24:50.000-06:00   
1  2021-01-01T00:00:53.563-06:00  2020-12-31T19:48:00.000-06:00   
3  2021-01-01T00:01:23.378-06:00  2020-12-31T18:17:59.000-06:00   
4  2021-01-01T00:01:54.761-06:00  2020-12-31T19:01:10.000-06:00   
5  2021-01-01T00:01:58.278-06:00  2020-12-31T22:45:54.000-06:00   

                 date_record_end  date_deleted      size_mb  duration_seconds  \
0  2020-12-31T18:37:22.640-06:00           NaN   374.265789           752.640   
1  2020-12-31T20:12:20.000-06:00           NaN   726.314941          1460.000   
3  2020-12-31T19:01:59.528-06:00           NaN  1314.288627          2640.530   
4  2020-12-31T19:01:39.293-06:00           NaN    14.587191            29.293   
5  2020-12-31T22:47:01.215-06:00           NaN    33.327763            67.215   

  deletion_type         location  latitude  longitude  police_district  \
0           NaN  (29.93, -90.10)     29.93     -90.10              6.0   
1           NaN  (29.96, -90.10)     29.96     -90.10              6.0   
3           NaN  (29.95, -90.09)     29.95     -90.09              6.0   
4          User  (29.94, -90.08)     29.94     -90.08              6.0   
5           NaN  (29.94, -90.08)     29.94     -90.08              6.0   

                     geometry  
0  POINT (-90.10000 29.93000)  
1  POINT (-90.10000 29.96000)  
3  POINT (-90.09000 29.95000)  
4  POINT (-90.08000 29.94000)  
5  POINT (-90.08000 29.94000)

In [ ]:
print(neworleansSHP.total_bounds)

[-90.140074   29.866661  -89.6255221  30.19866  ]


In [ ]:
##xmin, ymin, xmax, ymax = neworleansSHP.total_bounds

##BWCmetaGeo = BWCmetaGEO.cx[xmin:ymin, xmax:ymax]

In [ ]:
metaJan= BWCmetaGEO.set_index('created_date_record_start').filter(like='2021-01', axis=0)
metaFeb= BWCmetaGEO.set_index('created_date_record_start').filter(like='2021-02', axis=0)
metaMar= BWCmetaGEO.set_index('created_date_record_start').filter(like='2021-03', axis=0)
metaApr= BWCmetaGEO.set_index('created_date_record_start').filter(like='2021-04', axis=0)
metaMay= BWCmetaGEO.set_index('created_date_record_start').filter(like='2021-05', axis=0)
metaJune= BWCmetaGEO.set_index('created_date_record_start').filter(like='2021-06', axis=0)
metaJuly=BWCmetaGEO.set_index('created_date_record_start').filter(like='2021-07', axis=0)
metaAug= BWCmetaGEO.set_index('created_date_record_start').filter(like='2021-08', axis=0)
metaSept= BWCmetaGEO.set_index('created_date_record_start').filter(like='2021-09', axis=0)
metaOct= BWCmetaGEO.set_index('created_date_record_start').filter(like='2021-10', axis=0)
metaNov= BWCmetaGEO.set_index('created_date_record_start').filter(like='2021-11', axis=0)
metaDec= BWCmetaGEO.set_index('created_date_record_start').filter(like='2021-12', axis=0)


In [ ]:
metaJan.shape

(33582, 15)

In [ ]:
##metaFeb= metaFeb.cx[xmin:ymin, xmax:ymax]

In [ ]:
metaJan.shape

(33582, 15)

In [ ]:
metaJan.head(10)

evidence_id  status  \
created_date_record_start                                                     
2021-01-01T00:40:47.000-06:00  8FD8C2ED-C505-40E8-8B82-A97F1407CDCF  Active   
2021-01-01T00:58:45.000-06:00  479DC73B-63D8-456F-A892-04308EB955D7  Active   
2021-01-01T02:08:06.000-06:00  623F3318-C19F-4043-927C-F82FA58A7C00  Active   
2021-01-01T02:06:01.000-06:00  B7C4FE45-C598-442F-BC72-231BA8F99753  Active   
2021-01-01T00:58:47.000-06:00  5EAD33D6-1EA3-4942-8414-E598E46C7CF3  Active   
2021-01-01T02:08:06.000-06:00  CE421969-8E81-46F4-A75A-A7232F3B0C3B  Active   
2021-01-01T02:08:05.000-06:00  3F0BFB5C-7897-4900-9ED5-8DB1C89371B0  Active   
2021-01-01T00:17:49.000-06:00  B8D61768-1276-4DFB-84B4-DEA983AAD677  Active   
2021-01-01T00:14:03.000-06:00  C97B9AFA-82E8-4720-9650-515A9615EFFC  Active   
2021-01-01T00:12:56.000-06:00  D82E1067-B709-42ED-992F-A525F0429154  Active   

                                                                           title  \
created_date_record_start                                                          
2021-01-01T00:40:47.000-06:00                                        200 Bourbon   
2021-01-01T00:58:45.000-06:00                                        200 Bourbon   
2021-01-01T02:08:06.000-06:00                                    Bourbon @ Conti   
2021-01-01T02:06:01.000-06:00                                     Bourbon @conti   
2021-01-01T00:58:47.000-06:00                                         Accidental   
2021-01-01T02:08:06.000-06:00                              BOURBON ST / CONTI ST   
2021-01-01T02:08:05.000-06:00                                  Bourbon And Conti   
2021-01-01T00:17:49.000-06:00  I-610 East And Elysian Fields / I-10 West And ...   
2021-01-01T00:14:03.000-06:00                  Axon Body 3 Video 2021-01-01 0014   
2021-01-01T00:12:56.000-06:00                                          739 Conti   

                              id_external                  date_uploaded  \
created_date_record_start                                                  
2021-01-01T00:40:47.000-06:00  A-00000-21  2021-01-01T02:35:45.422-06:00   
2021-01-01T00:58:45.000-06:00  A-00109-21  2021-01-01T02:36:47.204-06:00   
2021-01-01T02:08:06.000-06:00  A-00176-21  2021-01-01T02:37:32.084-06:00   
2021-01-01T02:06:01.000-06:00  A-00169-21  2021-01-01T02:37:56.458-06:00   
2021-01-01T00:58:47.000-06:00  A-00000-20  2021-01-01T02:39:14.933-06:00   
2021-01-01T02:08:06.000-06:00  A-00000-20  2021-01-01T02:41:49.608-06:00   
2021-01-01T02:08:05.000-06:00  A-00169-21  2021-01-01T02:43:17.434-06:00   
2021-01-01T00:17:49.000-06:00  L-37903-20  2021-01-01T02:44:51.375-06:00   
2021-01-01T00:14:03.000-06:00         NaN  2021-01-01T02:46:02.935-06:00   
2021-01-01T00:12:56.000-06:00  A-00019-21  2021-01-01T02:47:51.443-06:00   

                                             date_record_end  date_deleted  \
created_date_record_start                                                    
2021-01-01T00:40:47.000-06:00  2021-01-01T00:44:02.932-06:00           NaN   
2021-01-01T00:58:45.000-06:00  2021-01-01T01:05:45.675-06:00           NaN   
2021-01-01T02:08:06.000-06:00  2021-01-01T02:09:47.610-06:00           NaN   
2021-01-01T02:06:01.000-06:00  2021-01-01T02:14:27.387-06:00           NaN   
2021-01-01T00:58:47.000-06:00  2021-01-01T01:05:20.477-06:00           NaN   
2021-01-01T02:08:06.000-06:00  2021-01-01T02:13:14.798-06:00           NaN   
2021-01-01T02:08:05.000-06:00  2021-01-01T02:14:27.180-06:00           NaN   
2021-01-01T00:17:49.000-06:00  2021-01-01T00:19:48.640-06:00           NaN   
2021-01-01T00:14:03.000-06:00  2021-01-01T00:17:49.017-06:00           NaN   
2021-01-01T00:12:56.000-06:00  2021-01-01T00:17:49.030-06:00           NaN   

                                  size_mb  duration_seconds deletion_type  \
created_date_record_start                                                   
2021-01-01T00:40:47.000-06:00   97.029998           195.932           NaN   
2021-01-01T00:58:

In [ ]:
metaJanGeo = gpd.GeoDataFrame(
    metaJan, geometry=BWCmetaGEO.geometry)
metaFebGeo = gpd.GeoDataFrame(
    metaFeb, geometry=BWCmetaGEO.geometry)
metaMarGeo = gpd.GeoDataFrame(
    metaMar, geometry=BWCmetaGEO.geometry)
metaAprGeo = gpd.GeoDataFrame(
    metaApr, geometry=BWCmetaGEO.geometry)
metaMayGeo = gpd.GeoDataFrame(
    metaMay, geometry=BWCmetaGEO.geometry)
metaJuneGeo = gpd.GeoDataFrame(
    metaJune, geometry=BWCmetaGEO.geometry)
metaJulyGeo = gpd.GeoDataFrame(
    metaJuly, geometry=BWCmetaGEO.geometry)
metaAugGeo = gpd.GeoDataFrame(
    metaAug, geometry=BWCmetaGEO.geometry)
metaSeptGeo = gpd.GeoDataFrame(
    metaSept, geometry=BWCmetaGEO.geometry)
metaOctGeo = gpd.GeoDataFrame(
    metaOct, geometry=BWCmetaGEO.geometry)
metaNovGeo = gpd.GeoDataFrame(
    metaNov, geometry=BWCmetaGEO.geometry)
metaDecGeo = gpd.GeoDataFrame(
    metaDec, geometry=BWCmetaGEO.geometry)

In [ ]:
metaJanGeo.crs
metaFebGeo.crs
metaMarGeo.crs
metaAprGeo.crs
metaMayGeo.crs
metaJuneGeo.crs
metaJulyGeo.crs
metaAugGeo.crs
metaSeptGeo.crs
metaOctGeo.crs
metaNovGeo.crs
metaDecGeo.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

### https://gis.stackexchange.com/questions/306674/geopandas-spatial-join-and-count

In [ ]:
basemap = alt.Chart(neworleansSHP).mark_geoshape(
    width=1000,
    height=1000,
    fill='lightgray',
    stroke='darkgray',
    strokeWidth=0.5
).project(
    type='conicConformal',
    parallels=[31 + 10 / 60, 32 + 40 / 60],
    rotate=[92 + 30 / 60, 0],
)

In [ ]:
janMap = alt.Chart(metaJanGeo).mark_circle(size=2).encode(
      latitude= 'latitude',
      longitude='longitude',
) 
juneMap = alt.Chart(metaJuneGeo).mark_circle(size=2).encode(
    latitude='latitude',
    longitude='longitude'
    )

decMap = alt.Chart(metaDecGeo).mark_circle(size=2).encode(
      latitude= 'latitude',
      longitude='longitude',
)

febMap = alt.Chart(metaFebGeo).mark_circle(size=2).encode(
      latitude= 'latitude',
      longitude='longitude',
)

https://gis.stackexchange.com/questions/266730/filter-by-bounding-box-in-geopandas

In [ ]:
alt.data_transformers.enable('default', max_rows=35000)

DataTransformerRegistry.enable('default')

In [ ]:
metaJanGeo.shape

(33582, 15)

In [ ]:
basemap + decMap

/usr/local/lib/python3.7/dist-packages/geopandas/array.py:918: RuntimeWarning: All-NaN slice encountered
  np.nanmin(b[:, 0]),  # minx
/usr/local/lib/python3.7/dist-packages/geopandas/array.py:919: RuntimeWarning: All-NaN slice encountered
  np.nanmin(b[:, 1]),  # miny
/usr/local/lib/python3.7/dist-packages/geopandas/array.py:920: RuntimeWarning: All-NaN slice encountered
  np.nanmax(b[:, 2]),  # maxx
/usr/local/lib/python3.7/dist-packages/geopandas/array.py:921: RuntimeWarning: All-NaN slice encountered
  np.nanmax(b[:, 3]),  # maxy
/usr/local/lib/python3.7/dist-packages/geopandas/array.py:918: RuntimeWarning: All-NaN slice encountered
  np.nanmin(b[:, 0]),  # minx
/usr/local/lib/python3.7/dist-packages/geopandas/array.py:919: RuntimeWarning: All-NaN slice encountered
  np.nanmin(b[:, 1]),  # miny
/usr/local/lib/python3.7/dist-packages/geopandas/array.py:920: RuntimeWarning: All-NaN slice encountered
  np.nanmax(b[:, 2]),  # maxx
/usr/local/lib/python3.7/dist-packages/geopandas/array.

alt.LayerChart(...)

In [ ]:
!apt-get install -qq curl g++ make

In [ ]:
!curl -L http://download.osgeo.org/libspatialindex/spatialindex-src-1.8.5.tar.gz | tar xz

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  556k  100  556k    0     0   432k      0  0:00:01  0:00:01 --:--:--  432k


In [ ]:
import os
os.chdir('spatialindex-src-1.8.5')
!./configure
!make
!make install
!pip install rtree
!ldconfig
from rtree import index
from rtree.index import Rtree

libtool: compile:  g++ -DPACKAGE_NAME=\"spatialindex\" -DPACKAGE_TARNAME=\"spatialindex-src\" -DPACKAGE_VERSION=\"1.8.5\" "-DPACKAGE_STRING=\"spatialindex 1.8.5\"" -DPACKAGE_BUGREPORT=\"mhadji@gmail.com\" -DPACKAGE_URL=\"\" -DSTDC_HEADERS=1 -DHAVE_SYS_TYPES_H=1 -DHAVE_SYS_STAT_H=1 -DHAVE_STDLIB_H=1 -DHAVE_STRING_H=1 -DHAVE_MEMORY_H=1 -DHAVE_STRINGS_H=1 -DHAVE_INTTYPES_H=1 -DHAVE_STDINT_H=1 -DHAVE_UNISTD_H=1 -DHAVE_DLFCN_H=1 -DLT_OBJDIR=\".libs/\" -DPACKAGE=\"spatialindex-src\" -DVERSION=\"1.8.5\" -DHAVE_FCNTL_H=1 -DHAVE_UNISTD_H=1 -DHAVE_SYS_TYPES_H=1 -DHAVE_SYS_STAT_H=1 -DHAVE_PTHREAD_H=1 -DHAVE_SYS_RESOURCE_H=1 -DHAVE_SYS_TIME_H=1 -DHAVE_STDINT_H=1 -DHAVE_FEATURES_H=1 -DHAVE_GETTIMEOFDAY=1 -DHAVE_MEMSET=1 -DHAVE_MEMCPY=1 -DHAVE_BCOPY=1 -DHAVE_SRAND48=1 -I. -I../../include -I../../include/capi -Wall -Wno-long-long -pedantic -std=c++98 -O2 -DNDEBUG -MT sidx_api.lo -MD -MP -MF .deps/sidx_api.Tpo -c sidx_api.cc -o sidx_api.o >/dev/null 2>&1
Makefile:382: recipe for target 'sidx_api.lo' f

In [ ]:
import rtree

In [ ]:
BWCmetaGEO.to_crs(4326)

evidence_id  status  \
0       92F109F4-DC36-42C3-9FFE-2EB223A5F67F  Active   
1       FAC99FF5-6388-4CF6-9FCD-51914BEDA938  Active   
3       A751D1B2-CF80-4B22-A11A-F08DE7340219  Active   
4       0EA9EFD1-31E2-42A1-8D78-AE3459CDC44A  Active   
5       2BA89B28-6E32-4156-BBBC-40922D1FA271  Active   
...                                      ...     ...   
119405  139E62FE-D2A7-4115-BAFF-60209A5E56DE  Active   
119406  1E7B03C5-4769-47B1-A58E-8689F0D931C0  Active   
119407  108F0670-09A5-4CBF-9FD3-16DC315F4B41  Active   
119408  44A95DF8-8782-45C5-BF57-4CB5E244DD85  Active   
119409  305EA71A-4DA4-4809-9946-413CB0C3A45E  Active   

                                              title id_external  \
0                                   1421 GEN TAYLOR  L-37827-20   
1                                  929 S TELEMACHUS  L-37936-20   
3                 Axon Body 3 Video 2020-12-31 1817         NaN   
4                                    SIXTH DISTRICT  L-00000-20   
5                                        Accidental   L-0000-20   
...                                             ...         ...   
119405  Axon Body 3 Video 2021-12-02 1902 X60311919         NaN   
119406  Axon Body 3 Video 2021-12-01 1956 X6031768F         NaN   
119407  Axon Body 3 Video 2021-12-01 2037 X6031768F         NaN   
119408  Axon Body 3 Video 2021-12-02 2000 X60311919         NaN   
119409                             715 S. Broad St   J-33616-21   

                        date_uploaded      created_date_record_start  \
0       2021-01-01T00:00:38.795-06:00  2020-12-31T18:24:50.000-06:00   
1       2021-01-01T00:00:53.563-06:00  2020-12-31T19:48:00.000-06:00   
3       2021-01-01T00:01:23.378-06:00  2020-12-31T18:17:59.000-06:00   
4       2021-01-01T00:01:54.761-06:00  2020-12-31T19:01:10.000-06:00   
5       2021-01-01T00:01:58.278-06:00  2020-12-31T22:45:54.000-06:00   
...                               ...                            ...   
119405  2021-12-13T11:40:07.986-06:00  2021-12-02T19:02:48.000-06:00   
119406  2021-12-16T01:10:27.698-06:00  2021-12-01T19:56:26.000-06:00   
119407  2021-12-16T01:15:39.168-06:00  2021-12-01T20:37:29.000-06:00   
119408  2021-12-17T03:02:52.528-06:00  2021-12-02T20:00:37.000-06:00   
119409  2021-12-18T19:46:57.661-06:00  2021-12-01T12:30:14.000-06:00   

                      date_record_end  date_deleted      size_mb  \
0       2020-12-31T18:37:22.640-06:00           NaN   374.265789   
1       2020-12-31T20:12:20.000-06:00           NaN   726.314941   
3       2020-12-31T19:01:59.528-06:00           NaN  1314.288627   
4       2020-12-31T19:01:39.293-06:00           NaN    14.587191   
5       2020-12-31T22:47:01.215-06:00           NaN    33.327763   
...                               ...           ...          ...   
119405  2021-12-02T19:50:32.236-06:00           NaN  1423.516988   
119406  2021-12-01T20:18:36.025-06:00           NaN   658.933315   
119407  2021-12-01T21:00:39.575-06:00           NaN   690.204750   
119408  2021-12-02T20:11:32.276-06:00           NaN   325.627728   
119409  2021-12-01T13:12:46.657-06:00           NaN  1268.771606   

        duration_seconds deletion_type  \
0                752.640           NaN   
1               1460.000           NaN   
3               2640.530           NaN   
4                 29.293          User   
5                 67.215           NaN   
...                  ...           ...   
119405          2864.230           NaN   
119406          1330.020           NaN   
119407          1390.570           NaN   
119408           655.270           NaN   
119409          2552.650           NaN   

                                       location   latitude  longitude  \
0                               (29.93, -90.10)  29.930000 -90.100000   
1                               (29.96, -90.10)  29.960000 -90.100000   
3                               (29.95, -90.09)  29.950000 -90.090000   
4                               (29.94, -90.08)  29.940000 -90.080000   
5  

In [ ]:
metaJoin = gpd.sjoin(neworleansSHP, BWCmetaGEO) #Spatial join Points to polygons
##dfpivot = pd.pivot_table(dfsjoin,index='GEOID',columns='Food',aggfunc={'Food':len})
#dfpivot.columns = dfpivot.columns.droplevel()

#dfpolynew = polys.merge(dfpivot, how='left', on='PolyID')

In [ ]:
metaJoin.head()

STATEFP COUNTYFP TRACTCE              AFFGEOID        GEOID NAME  \
16      22      071  004600  1400000US22071004600  22071004600   46   
16      22      071  004600  1400000US22071004600  22071004600   46   
16      22      071  004600  1400000US22071004600  22071004600   46   
16      22      071  004600  1400000US22071004600  22071004600   46   
16      22      071  004600  1400000US22071004600  22071004600   46   

           NAMELSAD STUSPS      NAMELSADCO STATE_NAME  ...  \
16  Census Tract 46     LA  Orleans Parish  Louisiana  ...   
16  Census Tract 46     LA  Orleans Parish  Louisiana  ...   
16  Census Tract 46     LA  Orleans Parish  Louisiana  ...   
16  Census Tract 46     LA  Orleans Parish  Louisiana  ...   
16  Census Tract 46     LA  Orleans Parish  Louisiana  ...   

        created_date_record_start                date_record_end  \
16  2021-02-13T00:24:36.000-06:00  2021-02-13T00:26:04.257-06:00   
16  2021-02-13T00:23:47.000-06:00  2021-02-13T00:26:10.340-06:00   
16  2021-02-11T06:15:30.000-06:00  2021-02-11T06:27:44.408-06:00   
16  2021-01-09T11:06:15.000-06:00  2021-01-09T11:30:24.348-06:00   
16  2021-01-19T09:22:21.000-06:00  2021-01-19T09:44:35.178-06:00   

    date_deleted     size_mb  duration_seconds deletion_type         location  \
16           NaN   43.711766            88.257           NaN  (29.98, -90.09)   
16           NaN   71.050348           143.340           NaN  (29.98, -90.09)   
16           NaN  364.919438           734.408           NaN  (29.98, -90.09)   
16           NaN  719.502159          1449.350           NaN  (29.98, -90.09)   
16           NaN  663.593026          1334.180           NaN  (29.98, -90.09)   

   latitude longitude police_district  
16    29.98    -90.09             1.0  
16    29.98    -90.09             1.0  
16    29.98    -90.09             1.0  
16    29.98    -90.09             1.0  
16    29.98    -90.09             1.0  

[5 rows x 30 columns]

In [ ]:
metaJoin['dur_median'] = metaJoin['duration_seconds'] / 60

In [ ]:
metaJoin.head(1)

STATEFP COUNTYFP TRACTCE              AFFGEOID        GEOID NAME  \
16      22      071  004600  1400000US22071004600  22071004600   46   

           NAMELSAD STUSPS      NAMELSADCO STATE_NAME  ...  \
16  Census Tract 46     LA  Orleans Parish  Louisiana  ...   

                  date_record_end  date_deleted    size_mb duration_seconds  \
16  2021-02-13T00:26:04.257-06:00           NaN  43.711766           88.257   

    deletion_type         location latitude longitude police_district  \
16            NaN  (29.98, -90.09)    29.98    -90.09             1.0   

   dur_median  
16    1.47095  

[1 rows x 31 columns]

In [ ]:
neworleansSHP.head()

In [ ]:
tractList = metaJoin['NAME'].tolist()
print (tractList)


['46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46', '46

In [ ]:
tracts = metaJoin.TRACTCE.unique()
print(tracts)


['004600' '003302' '003400' '011600' '009400' '008300' '009900' '002700'
 '001302' '004800' '001745' '000400' '002600' '000611' '002504' '012101'
 '012102' '008600' '000901' '010900' '013900' '004100' '001737' '011500'
 '004000' '013600' '003304' '002100' '005603' '001750' '007101' '013702'
 '013502' '000620' '002800' '002501' '010100' '000702' '003500' '003000'
 '000701' '005500' '001741' '010800' '001754' '003303' '001402' '012500'
 '001756' '014000' '008200' '008500' '007800' '001720' '006500' '000800'
 '000619' '009600' '001600' '009700' '014101' '001739' '004500' '011400'
 '005601' '001724' '001900' '007200' '006000' '007501' '005000' '002200'
 '005604' '007000' '000902' '002300' '001800' '009000' '008400' '006900'
 '000612' '001736' '004401' '010300' '000904' '001746' '001100' '014500'
 '013302' '013701' '013501' '001740' '012300' '000601' '000200' '000603'
 '013400' '012800' '001200' '003308' '003800' '007502' '013000' '000602'
 '000618' '013100' '005400' '000300' '006300' '0076

In [ ]:
tracts.shape

In [ ]:
counts= metaJoin.NAME.value_counts()

In [ ]:
counts.head()

In [ ]:
basemap

In [ ]:
joinedBWC = metaJoin.groupby(['TRACTCE']).agg({'GEOID':'min','latitude':'min','longitude':'min', 'duration_seconds':'sum', 'dur_median': 'median', 'size_mb':'count'}).reset_index()

In [ ]:
joinedBWC.head()

TRACTCE        GEOID   latitude  longitude  duration_seconds  dur_median  \
0  000100  22071000100  29.948683 -90.053786        296453.402    9.550650   
1  000200  22071000200  29.941287 -90.055085         68619.492    7.288025   
2  000300  22071000300  29.936380 -90.053301        357316.273   16.457583   
3  000400  22071000400  29.938050 -90.046216        880926.565    8.567500   
4  000601  22071000601  29.929256 -90.043264        321999.772   11.192283   

   size_mb  
0      233  
1       82  
2      211  
3      718  
4      232

In [ ]:
joinedBWC['durXcount'] = joinedBWC['duration_seconds'] /60 * joinedBWC['size_mb']

In [ ]:
joinedBWC.head()

TRACTCE        GEOID   latitude  longitude  duration_seconds  dur_median  \
0  000100  22071000100  29.948683 -90.053786        296453.402    9.550650   
1  000200  22071000200  29.941287 -90.055085         68619.492    7.288025   
2  000300  22071000300  29.936380 -90.053301        357316.273   16.457583   
3  000400  22071000400  29.938050 -90.046216        880926.565    8.567500   
4  000601  22071000601  29.929256 -90.043264        321999.772   11.192283   

   size_mb     durXcount  
0      233  1.151227e+06  
1       82  9.377997e+04  
2      211  1.256562e+06  
3      718  1.054175e+07  
4      232  1.245066e+06

In [ ]:
bwcCTmerge = joinedBWC.merge(neworleansSHP, on='GEOID')

In [ ]:
bwcCTmerge.head()

TRACTCE_x        GEOID   latitude  longitude  duration_seconds     dur_mean  \
0    000100  22071000100  29.948683 -90.053786        296453.402  1272.332197   
1    000200  22071000200  29.941287 -90.055085         68619.492   836.823073   
2    000300  22071000300  29.936380 -90.053301        357316.273  1693.442052   
3    000400  22071000400  29.938050 -90.046216        880926.565  1226.917221   
4    000601  22071000601  29.929256 -90.043264        321999.772  1387.930052   

   dur_median  size_mb     durXcount STATEFP  ...              AFFGEOID  NAME  \
0    9.550650      233  1.151227e+06      22  ...  1400000US22071000100     1   
1    7.288025       82  9.377997e+04      22  ...  1400000US22071000200     2   
2   16.457583      211  1.256562e+06      22  ...  1400000US22071000300     3   
3    8.567500      718  1.054175e+07      22  ...  1400000US22071000400     4   
4   11.192283      232  1.245066e+06      22  ...  1400000US22071000601  6.01   

            NAMELSAD STUSPS      NAMELSADCO STATE_NAME LSAD    ALAND  AWATER  \
0     Census Tract 1     LA  Orleans Parish  Louisiana   CT   717245  505586   
1     Census Tract 2     LA  Orleans Parish  Louisiana   CT   499389  167245   
2     Census Tract 3     LA  Orleans Parish  Louisiana   CT   634745       0   
3     Census Tract 4     LA  Orleans Parish  Louisiana   CT  1496645  200524   
4  Census Tract 6.01     LA  Orleans Parish  Louisiana   CT   485434       0   

                                            geometry  
0  POLYGON ((-90.05867 29.95390, -90.05697 29.956...  
1  POLYGON ((-90.05857 29.94764, -90.05447 29.949...  
2  POLYGON ((-90.05368 29.94114, -90.05190 29.941...  
3  POLYGON ((-90.04651 29.93489, -90.04610 29.941...  
4  POLYGON ((-90.04348 29.93691, -90.04255 29.937...  

[5 rows x 22 columns]

In [ ]:
bwcCTmerge.rename(columns={'size_mb':'Activation Count'},inplace=True)

In [ ]:
bwcCTmergeGeo = gpd.GeoDataFrame(bwcCTmerge)

In [ ]:
bwcCTmergeGeo.head

<bound method NDFrame.head of     TRACTCE_x        GEOID   latitude  longitude  duration_seconds  \
0      000100  22071000100  29.948683 -90.053786        296453.402   
1      000200  22071000200  29.941287 -90.055085         68619.492   
2      000300  22071000300  29.936380 -90.053301        357316.273   
3      000400  22071000400  29.938050 -90.046216        880926.565   
4      000601  22071000601  29.929256 -90.043264        321999.772   
..        ...          ...        ...        ...               ...   
179    014400  22071014400  29.915826 -90.128811         75443.890   
180    014500  22071014500  29.958509 -90.098385        221464.817   
181    980000  22071980000  29.983248 -90.102593        361417.266   
182    980100  22071980100  29.980000 -90.020000         49228.144   
183    990000  22071990000  30.160000 -89.850000         24536.340   

     dur_median  Activation Count     durXcount STATEFP COUNTYFP  ...  \
0      9.550650               233  1.151227e+06      22 

In [ ]:
sortedbwcCTmerge = bwcCTmergeGeo.sort_values('Activation Count', axis=0, ascending=False, inplace=False, kind='quicksort', na_position='last', ignore_index=False, key=None)

In [ ]:
sortedbwcCTmerge = gpd.GeoDataFrame(sortedbwcCTmerge)

In [ ]:
sortedbwcCTmerge.head()

TRACTCE_x        GEOID   latitude  longitude  duration_seconds  \
166    013400  22071013400  29.937672 -90.085001       6968337.701   
90     003900  22071003900  29.958981 -90.074442       3484383.937   
48     001747  22071001747  30.027057 -89.975669       3219135.338   
8      000605  22071000605  29.938685 -90.038673       1598718.972   
173    013900  22071013900  29.935419 -90.080773       2488388.124   

     dur_median  Activation Count     durXcount STATEFP COUNTYFP  ...  \
166    6.950683              7512  8.724359e+08      22      071  ...   
90     3.180933              4773  2.771827e+08      22      071  ...   
48     2.575575              4638  2.488392e+08      22      071  ...   
8      2.327783              4015  1.069809e+08      22      071  ...   
173    2.981267              3544  1.469808e+08      22      071  ...   

                 AFFGEOID   NAME            NAMELSAD STUSPS      NAMELSADCO  \
166  1400000US22071013400    134    Census Tract 134     LA  Orleans Parish   
90   1400000US22071003900     39     Census Tract 39     LA  Orleans Parish   
48   1400000US22071001747  17.47  Census Tract 17.47     LA  Orleans Parish   
8    1400000US22071000605   6.05   Census Tract 6.05     LA  Orleans Parish   
173  1400000US22071013900    139    Census Tract 139     LA  Orleans Parish   

    STATE_NAME LSAD    ALAND   AWATER  \
166  Louisiana   CT  2618982   406589   
90   Louisiana   CT   587302        0   
48   Louisiana   CT  7119930   344001   
8    Louisiana   CT  1744349  1011032   
173  Louisiana   CT   516381        0   

                                              geometry  
166  POLYGON ((-90.08519 29.95043, -90.08155 29.954...  
90   POLYGON ((-90.07474 29.96220, -90.07334 29.963...  
48   POLYGON ((-89.97346 30.03856, -89.97179 30.039...  
8    POLYGON ((-90.03866 29.94716, -90.03861 29.948...  
173  POLYGON ((-90.07872 29.94189, -90.07954 29.942...  

[5 rows x 21 columns]

In [ ]:
sortedbwcCTmerge['geometry']

166    POLYGON ((-90.08519 29.95043, -90.08155 29.954...
90     POLYGON ((-90.07474 29.96220, -90.07334 29.963...
48     POLYGON ((-89.97346 30.03856, -89.97179 30.039...
8      POLYGON ((-90.03866 29.94716, -90.03861 29.948...
173    POLYGON ((-90.07872 29.94189, -90.07954 29.942...
                             ...                        
146    POLYGON ((-90.12794 29.92144, -90.12748 29.922...
141    POLYGON ((-90.11480 29.92194, -90.11429 29.923...
156    POLYGON ((-90.13913 29.93030, -90.13907 29.932...
183    POLYGON ((-90.11937 30.03664, -90.10812 30.164...
33     POLYGON ((-90.03542 29.98379, -90.02979 29.982...
Name: geometry, Length: 184, dtype: geometry

In [ ]:
sortedbwcCTmerge.to_file("sortedbwcCTmerge.geojson", na='drop', driver="GeoJSON")

In [ ]:
sortedbwcCTmerge = sortedbwcCTmerge.set_crs('epsg:4326')

In [ ]:
sortedbwcCTmerge.to_file("sortedbwcCTmerge.geojson", na='drop', driver="GeoJSON")

In [ ]:
sortedbwcCTmerge.shape

(184, 21)

In [ ]:
noBWCmap = alt.Chart(sortedbwcCTmerge).mark_geoshape().encode(
    color=alt.Color('Activation Count:Q',
      legend=alt.Legend(title='2021 Body Camera Activations'),
      scale=alt.Scale(scheme='blues',
        domain=[0,10000])),
    tooltip=[alt.Tooltip('NAME',title='Census Tract'),
      alt.Tooltip('Activation Count',title='Activation Count')]
).project(
   type='conicConformal',
    parallels=[31 + 10 / 60, 32 + 40 / 60],
    rotate=[92 + 30 / 60, 0],
).properties(
    title='Body Worn Camera Activation per Census District 2021',
    width=700,
    height=450
).configure_view(
    strokeWidth=1
)

noBWCmap

alt.Chart(...)

In [ ]:
sortedbwcCTmerge['quantiles'] = pd.qcut(sortedbwcCTmerge['Activation Count'], 5, labels=['0 - 20 percentile','20 - 40 percentile','40 - 60 percentile','60 - 80 percentile','80 - 100 percentile'])

In [ ]:
sortedbwcCTmerge.tail()

TRACTCE_x        GEOID   latitude  longitude  duration_seconds  \
146    011500  22071011500  29.919287 -90.127526         26506.564   
141    010800  22071010800  29.921506 -90.114462         21005.386   
156    012500  22071012500  29.929464 -90.134407         19313.679   
183    990000  22071990000  30.160000 -89.850000         24536.340   
33     001600  22071001600  29.979855 -90.030239           741.413   

     dur_median  Activation Count     durXcount STATEFP COUNTYFP  ...  NAME  \
146    8.243333                27  11927.953800      22      071  ...   115   
141    7.201167                23   8052.064633      22      071  ...   108   
156    9.651558                20   6437.893000      22      071  ...   125   
183   12.764317                13   5316.207000      22      071  ...  9900   
33     6.178442                 2     24.713767      22      071  ...    16   

              NAMELSAD STUSPS      NAMELSADCO STATE_NAME LSAD   ALAND  \
146   Census Tract 115     LA  Orleans Parish  Louisiana   CT  456695   
141   Census Tract 108     LA  Orleans Parish  Louisiana   CT  397837   
156   Census Tract 125     LA  Orleans Parish  Louisiana   CT  632244   
183  Census Tract 9900     LA  Orleans Parish  Louisiana   CT       0   
33     Census Tract 16     LA  Orleans Parish  Louisiana   CT  143237   

        AWATER                                           geometry  \
146          0  POLYGON ((-90.12794 29.92144, -90.12748 29.922...   
141          0  POLYGON ((-90.11480 29.92194, -90.11429 29.923...   
156     648622  POLYGON ((-90.13913 29.93030, -90.13907 29.932...   
183  323404209  POLYGON ((-90.11937 30.03664, -90.10812 30.164...   
33           0  POLYGON ((-90.03542 29.98379, -90.02979 29.982...   

             quantiles  
146  0 - 20 percentile  
141  0 - 20 percentile  
156  0 - 20 percentile  
183  0 - 20 percentile  
33   0 - 20 percentile  

[5 rows x 22 columns]

In [ ]:
noBWCmap = alt.Chart(sortedbwcCTmerge).mark_geoshape().encode(
    color=alt.Color('quantiles:N',
      legend=alt.Legend(title='2021 Body Camera Activations'),
      scale=alt.Scale(scheme='reds',)
      ),
    tooltip=[alt.Tooltip('NAME',title='Census Tract'),
      alt.Tooltip('Activation Count',title='Activation Count')]
).project(
   type='conicConformal',
    parallels=[31 + 10 / 60, 32 + 40 / 60],
    rotate=[92 + 30 / 60, 0],
).properties(
    title='Body Worn Camera Activation per Census District 2021',
    width=700,
    height=450
).configure_view(
    strokeWidth=1
)

noBWCmap

alt.Chart(...)

In [ ]:
CENSUS_API_KEY = getpass('Enter your Census API Key:71289e596421a9cf9563bd9e9dd35077c4b3d076 ')

Enter your Census API Key:71289e596421a9cf9563bd9e9dd35077c4b3d076 ··········


In [ ]:
# Here, we are setting a variable (con) for making a call to this specific table.
con = cen.remote.APIConnection('ACSDT5Y2020',apikey=CENSUS_API_KEY)

In [ ]:
variables = con.variables


In [ ]:
columns = [
    'B01003_001', # Total Population
    'B19013_001',# Median Household Income
    'B03002_004' ] 

In [ ]:
columns_E = [i+'E' for i in columns]
columns_M = [i+'M' for i in columns]

In [ ]:
g_unit = 'tract'
g_filter = {'state':'22'}

In [ ]:
laIncome = con.query(columns_E + columns_M, geo_unit=g_unit, geo_filter=g_filter)

In [ ]:
laIncome.head()

B01003_001E B19013_001E B03002_004E B01003_001M B19013_001M B03002_004M  \
0        1586       55197         256         237       19900         146   
1        2634      107500         104         326       18819         154   
2        1439       36250         304         205       18458         168   
3        3178       50990         596         683        2301         237   
4        3556       62316        1075         757       20966         622   

  state county   tract  
0    22    051  024700  
1    22    051  024801  
2    22    051  024900  
3    22    051  025002  
4    22    051  025003

In [ ]:
noIncome = laIncome[laIncome['county'] == '071'] 

In [ ]:
noIncome.shape

(184, 9)

In [ ]:
noIncome['GEOID'] = noIncome['state'] + noIncome['county']

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [ ]:
noIncome.head(1)

B01003_001E B19013_001E B03002_004E B01003_001M B19013_001M B03002_004M  \
467        2591       79196         195         466       13207          92   

    state county   tract  GEOID  
467    22    071  000100  22071

In [ ]:
noIncome.rename(columns={'B01003_001E':'population','B19013_001E':'median income'}, inplace=True)

/usr/local/lib/python3.7/dist-packages/pandas/core/frame.py:5047: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


In [ ]:
sortedbwcCTmerge

TRACTCE_x        GEOID   latitude  longitude  duration_seconds  \
166    013400  22071013400  29.937672 -90.085001       6968337.701   
90     003900  22071003900  29.958981 -90.074442       3484383.937   
48     001747  22071001747  30.027057 -89.975669       3219135.338   
8      000605  22071000605  29.938685 -90.038673       1598718.972   
173    013900  22071013900  29.935419 -90.080773       2488388.124   
..        ...          ...        ...        ...               ...   
146    011500  22071011500  29.919287 -90.127526         26506.564   
141    010800  22071010800  29.921506 -90.114462         21005.386   
156    012500  22071012500  29.929464 -90.134407         19313.679   
183    990000  22071990000  30.160000 -89.850000         24536.340   
33     001600  22071001600  29.979855 -90.030239           741.413   

     dur_median  Activation Count     durXcount STATEFP COUNTYFP  ...   NAME  \
166    6.950683              7512  8.724359e+08      22      071  ...    134   
90     3.180933              4773  2.771827e+08      22      071  ...     39   
48     2.575575              4638  2.488392e+08      22      071  ...  17.47   
8      2.327783              4015  1.069809e+08      22      071  ...   6.05   
173    2.981267              3544  1.469808e+08      22      071  ...    139   
..          ...               ...           ...     ...      ...  ...    ...   
146    8.243333                27  1.192795e+04      22      071  ...    115   
141    7.201167                23  8.052065e+03      22      071  ...    108   
156    9.651558                20  6.437893e+03      22      071  ...    125   
183   12.764317                13  5.316207e+03      22      071  ...   9900   
33     6.178442                 2  2.471377e+01      22      071  ...     16   

               NAMELSAD STUSPS      NAMELSADCO STATE_NAME LSAD    ALAND  \
166    Census Tract 134     LA  Orleans Parish  Louisiana   CT  2618982   
90      Census Tract 39     LA  Orleans Parish  Louisiana   CT   587302   
48   Census Tract 17.47     LA  Orleans Parish  Louisiana   CT  7119930   
8     Census Tract 6.05     LA  Orleans Parish  Louisiana   CT  1744349   
173    Census Tract 139     LA  Orleans Parish  Louisiana   CT   516381   
..                  ...    ...             ...        ...  ...      ...   
146    Census Tract 115     LA  Orleans Parish  Louisiana   CT   456695   
141    Census Tract 108     LA  Orleans Parish  Louisiana   CT   397837   
156    Census Tract 125     LA  Orleans Parish  Louisiana   CT   632244   
183   Census Tract 9900     LA  Orleans Parish  Louisiana   CT        0   
33      Census Tract 16     LA  Orleans Parish  Louisiana   CT   143237   

        AWATER                                           geometry  \
166     406589  POLYGON ((-90.08519 29.95043, -90.08155 29.954...   
90           0  POLYGON ((-90.07474 29.96220, -90.07334 29.963...   
48      344001  POLYGON ((-89.97346 30.03856, -89.97179 30.039...   
8      1011032  POLYGON ((-90.03866 29.94716, -90.03861 29.948...   
173          0  POLYGON ((-90.07872 29.94189, -90.07954 29.942...   
..         ...                                                ...   
146          0  POLYGON ((-90.12794 29.92144, -90.12748 29.922...   
141          0  POLYGON ((-90.11480 29.92194, -90.11429 29.923...   
156     648622  POLYGON ((-90.13913 29.93030, -90.13907 29.932...   
183  323404209  POLYGON ((-90.11937 30.03664, -90.10812 30.164...   
33           0  POLYGON ((-90.03542 29.98379, -90.02979 29.982...   

               quantiles  
166  80 - 100 percentile  
90   80 - 100 percentile  
48   80 - 100 percentile  
8    80 - 100 percentile  
173  80 - 100 percentile  
..                   ...  
146    0 - 20 percentile  
141    0 - 20 percentile  
156    0 - 20 percentile  
183    0 - 20 percentile  
33     0 - 20 percentile  

[184 rows x 22 columns]

In [ ]:
sortedbwcCTmerge.head(1
)

tract        GEOID   latitude  longitude  duration_seconds  dur_median  \
166  013400  22071013400  29.937672 -90.085001       6968337.701    6.950683   

     Activation Count     durXcount STATEFP COUNTYFP  ... NAME  \
166              7512  8.724359e+08      22      071  ...  134   

             NAMELSAD STUSPS      NAMELSADCO STATE_NAME LSAD    ALAND  AWATER  \
166  Census Tract 134     LA  Orleans Parish  Louisiana   CT  2618982  406589   

                                              geometry            quantiles  
166  POLYGON ((-90.08519 29.95043, -90.08155 29.954...  80 - 100 percentile  

[1 rows x 21 columns]

In [ ]:
sortedbwcCTmerge.drop(columns='TRACTCE_y', inplace=True)
sortedbwcCTmerge.rename(columns={'TRACTCE_x':'tract'}, inplace=True)

In [ ]:
sortedbwcCTmerge.head(1)

tract        GEOID   latitude  longitude  duration_seconds  dur_median  \
166  013400  22071013400  29.937672 -90.085001       6968337.701    6.950683   

     Activation Count     durXcount STATEFP COUNTYFP  ... NAME  \
166              7512  8.724359e+08      22      071  ...  134   

             NAMELSAD STUSPS      NAMELSADCO STATE_NAME LSAD    ALAND  AWATER  \
166  Census Tract 134     LA  Orleans Parish  Louisiana   CT  2618982  406589   

                                              geometry            quantiles  
166  POLYGON ((-90.08519 29.95043, -90.08155 29.954...  80 - 100 percentile  

[1 rows x 21 columns]

In [ ]:
bwcMcensus = noIncome.merge(sortedbwcCTmerge, on='tract')

In [ ]:
bwcMcensus.rename(columns={'Population':'B01003_001M'}, inplace=True)

In [ ]:
bwcMcensus.rename(columns={'B19013_001E':'Income'}, inplace=True)

In [ ]:
bwcMcensus.head(1)

population median income B03002_004E B01003_001M B19013_001M B03002_004M  \
0       2591         79196         195         466       13207          92   

  state county   tract GEOID_x  ... NAME        NAMELSAD  STUSPS  \
0    22    071  000100   22071  ...    1  Census Tract 1      LA   

       NAMELSADCO  STATE_NAME  LSAD   ALAND  AWATER  \
0  Orleans Parish   Louisiana    CT  717245  505586   

                                            geometry           quantiles  
0  POLYGON ((-90.05867 29.95390, -90.05697 29.956...  40 - 60 percentile  

[1 rows x 30 columns]

In [ ]:
bwcMcensus.dtypes

population             int64
median income         object
B03002_004E           object
B01003_001M           object
B19013_001M           object
B03002_004M           object
state                 object
county                object
tract                 object
GEOID_x               object
GEOID_y               object
latitude             float64
longitude            float64
duration_seconds     float64
dur_median           float64
Activation Count       int64
durXcount            float64
STATEFP               object
COUNTYFP              object
AFFGEOID              object
NAME                  object
NAMELSAD              object
STUSPS                object
NAMELSADCO            object
STATE_NAME            object
LSAD                  object
ALAND                  int64
AWATER                 int64
geometry            geometry
quantiles           category
dtype: object

In [ ]:
bwcMcensus['Activation Count'].astype(int)


bwcMcensus['population'] = bwcMcensus['population'].astype('int') 

In [ ]:
bwcMcensus['population'].astype(int)


0      2591
1       918
2      1220
3      1979
4       886
       ... 
179    1643
180    2810
181      10
182       0
183       0
Name: population, Length: 184, dtype: int64

In [ ]:
bwcMcensus['B03002_004E'] = bwcMcensus['B03002_004E'].astype(int)


In [ ]:
bwcMcensus['percentageBlack']= bwcMcensus ['B03002_004E'] / bwcMcensus['population'] * 100

In [ ]:
bwcMcensus.dtypes

population             int64
median income         object
B03002_004E            int64
B01003_001M           object
B19013_001M           object
B03002_004M           object
state                 object
county                object
tract                 object
GEOID_x               object
GEOID_y               object
latitude             float64
longitude            float64
duration_seconds     float64
dur_median           float64
Activation Count       int64
durXcount            float64
STATEFP               object
COUNTYFP              object
AFFGEOID              object
NAME                  object
NAMELSAD              object
STUSPS                object
NAMELSADCO            object
STATE_NAME            object
LSAD                  object
ALAND                  int64
AWATER                 int64
geometry            geometry
percentageBlack      float64
popNorm              float64
dtype: object

In [ ]:
bwcMcensus['popNorm'] = bwcMcensus['Activation Count'] / bwcMcensus['population'] * 10

In [ ]:
bwcMcensus.head(10)

population median income  B03002_004E B01003_001M B19013_001M B03002_004M  \
0        2591         79196          195         466       13207          92   
1         918         29044          598         216        5761         214   
2        1220         33284         1095         292        3097         293   
3        1979         43333         1612         437       19166         402   
4         886         17525          868         175        4713         174   
5        2640         21972         2283         725       12112         748   
6        1149         19934          876         351        3823         312   
7        4060         25109         3627        1254       12682        1262   
8        1972         42130         1468         281       18624         318   
9        4022         67609         2327         586       11320         465   

  state county   tract GEOID_x  ...           NAMELSAD  STUSPS  \
0    22    071  000100   22071  ...     Census Tract 1      LA   
1    22    071  000200   22071  ...     Census Tract 2      LA   
2    22    071  000300   22071  ...     Census Tract 3      LA   
3    22    071  000400   22071  ...     Census Tract 4      LA   
4    22    071  000601   22071  ...  Census Tract 6.01      LA   
5    22    071  000602   22071  ...  Census Tract 6.02      LA   
6    22    071  000603   22071  ...  Census Tract 6.03      LA   
7    22    071  000604   22071  ...  Census Tract 6.04      LA   
8    22    071  000605   22071  ...  Census Tract 6.05      LA   
9    22    071  000606   22071  ...  Census Tract 6.06      LA   

       NAMELSADCO  STATE_NAME  LSAD    ALAND   AWATER  \
0  Orleans Parish   Louisiana    CT   717245   505586   
1  Orleans Parish   Louisiana    CT   499389   167245   
2  Orleans Parish   Louisiana    CT   634745        0   
3  Orleans Parish   Louisiana    CT  1496645   200524   
4  Orleans Parish   Louisiana    CT   485434        0   
5  Orleans Parish   Louisiana    CT  1657011        0   
6  Orleans Parish   Louisiana    CT   572760        0   
7  Orleans Parish   Louisiana    CT  1677098        0   
8  Orleans Parish   Louisiana    CT  1744349  1011032   
9  Orleans Parish   Louisiana    CT  1776178   616196   

                                            geometry percentageBlack  \
0  POLYGON ((-90.05867 29.95390, -90.05697 29.956...        7.526052   
1  POLYGON ((-90.05857 29.94764, -90.05447 29.949...       65.141612   
2  POLYGON ((-90.05368 29.94114, -90.05190 29.941...       89.754098   
3  POLYGON ((-90.04651 29.93489, -90.04610 29.941...       81.455280   
4  POLYGON ((-90.04348 29.93691, -90.04255 29.937...       97.968397   
5  POLYGON ((-90.04065 29.93767, -90.03748 29.937...       86.477273   
6  POLYGON ((-90.03108 29.92867, -90.02930 29.931...       76.240209   
7  POLYGON ((-90.02774 29.93622, -90.02761 29.938...       89.334975   
8  POLYGON ((-90.03866 29.94716, -90.03861 29.948...       74.442191   
9  POLYGON ((-90.01491 29.94298, -90.01387 29.947...       57.856788   

     popNorm  
0   0.899267  
1   0.893246  
2   1.729508  
3   3.628095  
4   2.618510  
5   2.140152  
6   4.595300  
7   2.226601  
8  20.360041  
9   1.103928  

[10 rows x 31 columns]

In [ ]:
bwcMcensus.drop(columns='quantiles', inplace=True)


In [ ]:
bwcMcensus['geometry']

0      POLYGON ((-90.05867 29.95390, -90.05697 29.956...
1      POLYGON ((-90.05857 29.94764, -90.05447 29.949...
2      POLYGON ((-90.05368 29.94114, -90.05190 29.941...
3      POLYGON ((-90.04651 29.93489, -90.04610 29.941...
4      POLYGON ((-90.04348 29.93691, -90.04255 29.937...
                             ...                        
179    POLYGON ((-90.12968 29.91812, -90.12978 29.919...
180    POLYGON ((-90.10029 29.96307, -90.09787 29.962...
181    POLYGON ((-90.10273 29.98412, -90.10211 29.989...
182    POLYGON ((-90.02215 29.99277, -90.01979 29.994...
183    POLYGON ((-90.11937 30.03664, -90.10812 30.164...
Name: geometry, Length: 184, dtype: geometry

In [ ]:
bwcMcensusGeo = gpd.GeoDataFrame(bwcMcensus)

In [ ]:
bwcMcensusGeo.drop([181, 182, 183])

population median income  B03002_004E B01003_001M B19013_001M  \
0          2591         79196          195         466       13207   
1           918         29044          598         216        5761   
2          1220         33284         1095         292        3097   
3          1979         43333         1612         437       19166   
4           886         17525          868         175        4713   
..          ...           ...          ...         ...         ...   
176         928         35394          662         124        2430   
177        1469         72200          299         275       12584   
178        2242         18664         1384         568        6937   
179        1643         71830          332         324       20822   
180        2810    -666666666         2290         376  -222222222   

    B03002_004M state county   tract GEOID_x  ...             NAMELSAD  \
0            92    22    071  000100   22071  ...       Census Tract 1   
1           214    22    071  000200   22071  ...       Census Tract 2   
2           293    22    071  000300   22071  ...       Census Tract 3   
3           402    22    071  000400   22071  ...       Census Tract 4   
4           174    22    071  000601   22071  ...    Census Tract 6.01   
..          ...   ...    ...     ...     ...  ...                  ...   
176         114    22    071  014102   22071  ...  Census Tract 141.02   
177         120    22    071  014200   22071  ...     Census Tract 142   
178         219    22    071  014300   22071  ...     Census Tract 143   
179         190    22    071  014400   22071  ...     Census Tract 144   
180         287    22    071  014500   22071  ...     Census Tract 145   

     STUSPS      NAMELSADCO  STATE_NAME  LSAD    ALAND   AWATER  \
0        LA  Orleans Parish   Louisiana    CT   717245   505586   
1        LA  Orleans Parish   Louisiana    CT   499389   167245   
2        LA  Orleans Parish   Louisiana    CT   634745        0   
3        LA  Orleans Parish   Louisiana    CT  1496645   200524   
4        LA  Orleans Parish   Louisiana    CT   485434        0   
..      ...             ...         ...   ...      ...      ...   
176      LA  Orleans Parish   Louisiana    CT   365689   295396   
177      LA  Orleans Parish   Louisiana    CT  1051112   785089   
178      LA  Orleans Parish   Louisiana    CT   474315        0   
179      LA  Orleans Parish   Louisiana    CT  1777409  1007284   
180      LA  Orleans Parish   Louisiana    CT   206718        0   

                                              geometry percentageBlack  \
0    POLYGON ((-90.05867 29.95390, -90.05697 29.956...        7.526052   
1    POLYGON ((-90.05857 29.94764, -90.05447 29.949...       65.141612   
2    POLYGON ((-90.05368 29.94114, -90.05190 29.941...       89.754098   
3    POLYGON ((-90.04651 29.93489, -90.04610 29.941...       81.455280   
4    POLYGON ((-90.04348 29.93691, -90.04255 29.937...       97.968397   
..                                                 ...             ...   
176  POLYGON ((-90.07521 29.92435, -90.07228 29.926...       71.336207   
177  POLYGON ((-90.10096 29.91715, -90.09761 29.917...       20.353982   
178  POLYGON ((-90.09638 29.93950, -90.09603 29.940...       61.730598   
179  POLYGON ((-90.12968 29.91812, -90.12978 29.919...       20.206939   
180  POLYGON ((-90.10029 29.96307, -90.09787 29.962...       81.494662   

      popNorm  
0    0.899267  
1    0.893246  
2    1.729508  
3    3.628095  
4    2.618510  
..        ...  
176  1.939655  
177  1.211709  
178  6.177520  
179  0.566038  
180  0.334520  

[181 rows x 31 columns]

In [ ]:
bwcMcensusGeo


population median income  B03002_004E B01003_001M B19013_001M  \
0          2591         79196          195         466       13207   
1           918         29044          598         216        5761   
2          1220         33284         1095         292        3097   
3          1979         43333         1612         437       19166   
4           886         17525          868         175        4713   
..          ...           ...          ...         ...         ...   
179        1643         71830          332         324       20822   
180        2810    -666666666         2290         376  -222222222   
181          10    -666666666            2          13  -222222222   
182           0    -666666666            0          14  -222222222   
183           0    -666666666            0          14  -222222222   

    B03002_004M state county   tract GEOID_x  ...           NAMELSAD  STUSPS  \
0            92    22    071  000100   22071  ...     Census Tract 1      LA   
1           214    22    071  000200   22071  ...     Census Tract 2      LA   
2           293    22    071  000300   22071  ...     Census Tract 3      LA   
3           402    22    071  000400   22071  ...     Census Tract 4      LA   
4           174    22    071  000601   22071  ...  Census Tract 6.01      LA   
..          ...   ...    ...     ...     ...  ...                ...     ...   
179         190    22    071  014400   22071  ...   Census Tract 144      LA   
180         287    22    071  014500   22071  ...   Census Tract 145      LA   
181           4    22    071  980000   22071  ...  Census Tract 9800      LA   
182          14    22    071  980100   22071  ...  Census Tract 9801      LA   
183          14    22    071  990000   22071  ...  Census Tract 9900      LA   

         NAMELSADCO  STATE_NAME  LSAD     ALAND     AWATER  \
0    Orleans Parish   Louisiana    CT    717245     505586   
1    Orleans Parish   Louisiana    CT    499389     167245   
2    Orleans Parish   Louisiana    CT    634745          0   
3    Orleans Parish   Louisiana    CT   1496645     200524   
4    Orleans Parish   Louisiana    CT    485434          0   
..              ...         ...   ...       ...        ...   
179  Orleans Parish   Louisiana    CT   1777409    1007284   
180  Orleans Parish   Louisiana    CT    206718          0   
181  Orleans Parish   Louisiana    CT   4961157     712738   
182  Orleans Parish   Louisiana    CT  31183156   11853446   
183  Orleans Parish   Louisiana    CT         0  323404209   

                                              geometry percentageBlack  \
0    POLYGON ((-90.05867 29.95390, -90.05697 29.956...        7.526052   
1    POLYGON ((-90.05857 29.94764, -90.05447 29.949...       65.141612   
2    POLYGON ((-90.05368 29.94114, -90.05190 29.941...       89.754098   
3    POLYGON ((-90.04651 29.93489, -90.04610 29.941...       81.455280   
4    POLYGON ((-90.04348 29.93691, -90.04255 29.937...       97.968397   
..                                                 ...             ...   
179  POLYGON ((-90.12968 29.91812, -90.12978 29.919...       20.206939   
180  POLYGON ((-90.10029 29.96307, -90.09787 29.962...       81.494662   
181  POLYGON ((-90.10273 29.98412, -90.10211 29.989...       20.000000   
182  POLYGON ((-90.02215 29.99277, -90.01979 29.994...             NaN   
183  POLYGON ((-90.11937 30.03664, -90.10812 30.164...             NaN   

        popNorm  
0      0.899267  
1      0.893246  
2      1.729508  
3      3.628095  
4      2.618510  
..          ...  
179    0.566038  
180    0.334520  
181  347.000000  
182         inf  
183         inf  

[184 rows x 31 columns]

In [ ]:
bwcMcensusGeo =bwcMcensusGeo.drop([181, 182, 183])

In [ ]:
bwcMcensusGeo

In [ ]:
bwcMcensusGeo.to_file("bwcMcensus.geojson", na='drop', driver="GeoJSON")

In [ ]:
bwcMcensusGeo = bwcMcensusGeo.set_crs('epsg:4326')

In [ ]:
bwcMcensusGeo['quantiles'] = pd.qcut(bwcMcensusGeo['Activation Count'], 5, labels=['0 - 20 percentile','20 - 40 percentile','40 - 60 percentile','60 - 80 percentile','80 - 100 percentile'])

In [ ]:
bwcMcensusGeo['quantilesNorm'] = pd.qcut(bwcMcensusGeo['popNorm'], 5, labels=['0 - 20 percentile','20 - 40 percentile','40 - 60 percentile','60 - 80 percentile','80 - 100 percentile'])

In [ ]:
bwcMcensusGeo['durationNorm'] = bwcMcensusGeo['duration_seconds'] / bwcMcensusGeo['population'] 

In [ ]:
bwcMcensusGeo['Majority Black'] = pd.qcut(bwcMcensusGeo['percentageBlack'], 2, labels=['no','yes'])

In [ ]:
bwcMcensusGeo['DurationQuant'] = pd.qcut(bwcMcensusGeo['durationNorm'], 5, labels=['0 - 20 percentile','20 - 40 percentile','40 - 60 percentile','60 - 80 percentile','80 - 100 percentile'])

In [ ]:
bwcMcensusGeo.dtypes

In [ ]:
bwcMcensusGeo.head(10)

In [ ]:
bwcMcensusGeo['quantilesNorm'].astype(object)

In [ ]:
bwcMcensusGeo['quantilesNorm'].astype(object)

In [ ]:
bwcMcensusGeo = gpd.GeoDataFrame(
    bwcMcensusGeo, geometry=bwcMcensusGeo.geometry)

In [ ]:
import fiona
fiona.supported_drivers

In [ ]:
with open('bwcMcensusGeo.json', 'w') as f:
  f.write(bwcMcensusGeo.to_json())

In [ ]:
!cat bwcMcensusGeo.json

cat: bwcMcensusGeo.json: No such file or directory


In [ ]:
from google.colab import files
files.download("bwcMcensusGeo.json")


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
bwcMcensusGeoCsv = bwcMcensusGeo.to_csv('bwcMcensusGeo.csv', index=False)

In [ ]:
from google.colab import files
files.download('bwcMcensusGeo.csv')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
bwcIncomePop = alt.Chart(bwcMcensus).mark_geoshape().encode(
    color=alt.Color('B19013_001E:Q', legend=alt.Legend(title='Median Household Income (Dollars)', format='$,.2r')),
    tooltip=[alt.Tooltip('NAME',title='County'),
      alt.Tooltip('B01003_001E',title='Population', format=','),
      alt.Tooltip('B19013_001E',title='Median Household Income', format='$,.2r')]
).properties(
    width=700,
    height=700,
    title='Median Household Income (MN)'
).project(
    type='conicConformal', 
    parallels=[45 + 37 / 60, 47 + 3 / 60], 
    rotate=[94 + 15 / 60, 0]
)


In [ ]:
bwcIncomePop = alt.Chart(bwcMcensusGeo).mark_geoshape().encode(
    color=alt.Color('quantiles:N',
      legend=alt.Legend(title='2021 Body Camera Activations'),
      scale=alt.Scale(scheme='reds',)
      ),
    tooltip=[alt.Tooltip('NAME',title='Census Tract'),
      alt.Tooltip('Activation Count',title='Activation Count'),
      alt.Tooltip('population',title='Population', format=','),
      alt.Tooltip('median income',title='Median Household Income', format='$,.2r')]

).project(
   type='conicConformal',
    parallels=[31 + 10 / 60, 32 + 40 / 60],
    rotate=[92 + 30 / 60, 0],
).properties(
    title='Body Worn Camera Activation per Census District 2021',
    width=700,
    height=450

)

In [ ]:
bwcMcensusGeo.dtypes

In [ ]:
bwcMcensusGeo.head()

NameError: ignored

In [ ]:
bwcDuration = alt.Chart(bwcMcensusGeo).mark_geoshape().encode(
    color=alt.Color('DurationQuant:N',
      legend=alt.Legend(title='Duration'),
      scale=alt.Scale(scheme='reds',)
      ),
    tooltip=[alt.Tooltip('NAME',title='Census Tract'),
      alt.Tooltip('Activation Count',title='Activation Count'),
      alt.Tooltip('population',title='Population', format=','),
      alt.Tooltip('median income',title='Median Household Income', format='$,.2r')]

).project(
   type='conicConformal',
    parallels=[31 + 10 / 60, 32 + 40 / 60],
    rotate=[92 + 30 / 60, 0],
).properties(
    title='2021 Body Camera Activations by duration',
    width=1400,
    height=900

)

In [ ]:
bwcDuration

In [ ]:
bwcIncomePopNorm = alt.Chart(bwcMcensusGeo).mark_geoshape().encode(
    color=alt.Color('quantilesNorm:N',
      legend=alt.Legend(title='2021 Body Camera Activations'),
      scale=alt.Scale(scheme='reds',)
      ),
    tooltip=[alt.Tooltip('NAME',title='Census Tract'),
      alt.Tooltip('Activation Count',title='Activation Count'),
      alt.Tooltip('population',title='Population', format=','),
      alt.Tooltip('median income',title='Median Household Income', format='$,.2r')]

).project(
   type='conicConformal',
    parallels=[31 + 10 / 60, 32 + 40 / 60],
    rotate=[92 + 30 / 60, 0],
).properties(
    title='Body Worn Camera Activation per Census District 2021 (rankings adjusted for population)',
    width=1400,
    height=900

)

In [ ]:
bwcIncomePopNorm

alt.Chart(...)

In [ ]:
popMap = alt.Chart(bwcMcensusGeo).mark_geoshape().encode(
   color=alt.Color('population:Q',
      legend=alt.Legend(title='population'),
      scale=alt.Scale(scheme='blues',
        domain=[0,5000])),
    tooltip=[alt.Tooltip('NAME',title='Census Tract'),
      alt.Tooltip('Activation Count',title='Activation Count'),
      alt.Tooltip('population',title='Population', format=','),
      alt.Tooltip('median income',title='Median Household Income', format='$,.2r')]

).project(
   type='conicConformal',
    parallels=[31 + 10 / 60, 32 + 40 / 60],
    rotate=[92 + 30 / 60, 0],
).properties(
    title='Population per Census District 2021',
    width=1400,
    height=900

)

popMap

alt.Chart(...)

In [ ]:
incomeMap = alt.Chart(bwcMcensusGeo).mark_geoshape().encode(
   color=alt.Color('median income:Q',
      legend=alt.Legend(title='Median Household Income'),
      scale=alt.Scale(scheme='greens',
        domain=[0,200000])),
    tooltip=[alt.Tooltip('NAME',title='Census Tract'),
      alt.Tooltip('Activation Count',title='Activation Count'),
      alt.Tooltip('population',title='Population', format=','),
      alt.Tooltip('median income',title='Median Household Income', format='$,.2r')]

).project(
   type='conicConformal',
    parallels=[31 + 10 / 60, 32 + 40 / 60],
    rotate=[92 + 30 / 60, 0],
).properties(
    title='Median Income per Census District 2021',
    width=1400,
    height=900

)

incomeMap

alt.Chart(...)

In [ ]:
alt.concat(alt.hconcat(incomeMap,bwcDuration)).configure_view(strokeWidth=0)

alt.ConcatChart(...)

In [ ]:
##df.groupby(df.date.dt.month)['activations'].count()
##df['activationId'] = 1
df.groupby(df.date.dt.month)['activationId'].sum()


NameError: ignored

In [ ]:
bwcMcensusGeo.dtypes

population             int64
median income         object
B03002_004E            int64
B01003_001M           object
B19013_001M           object
B03002_004M           object
state                 object
county                object
tract                 object
GEOID_x               object
GEOID_y               object
latitude             float64
longitude            float64
duration_seconds     float64
dur_median           float64
Activation Count       int64
durXcount            float64
STATEFP               object
COUNTYFP              object
AFFGEOID              object
NAME                  object
NAMELSAD              object
STUSPS                object
NAMELSADCO            object
STATE_NAME            object
LSAD                  object
ALAND                  int64
AWATER                 int64
geometry            geometry
percentageBlack      float64
popNorm              float64
quantiles           category
quantilesNorm       category
Majority Black      category
dtype: object

In [ ]:
majorityblackGDF = bwcMcensusGeo.dropna()

In [ ]:
majorityBlack = alt.Chart(majorityblackGDF).mark_geoshape().encode(
    color=alt.Color('Majority Black:N',
      legend=alt.Legend(title='Majority Black areas of new Orleans'),
      scale=alt.Scale(scheme='greys')
      ),
    tooltip=[alt.Tooltip('NAME',title='Census Tract'),
      alt.Tooltip('Activation Count',title='Activation Count'),
      alt.Tooltip('population',title='Population', format=','),
      alt.Tooltip('median income',title='Median Household Income', format='$,.2r'),
      alt.Tooltip('percentageBlack',title='African American')

      ]
      

).project(
   type='conicConformal',
    parallels=[31 + 10 / 60, 32 + 40 / 60],
    rotate=[92 + 30 / 60, 0],
).properties(
    title='Majority African American Areas 2021',
    width=1400,
    height=900

)

majorityBlack

alt.Chart(...)